In [11]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

pd.options.display.max_rows = 100
pd.options.display.max_seq_items = 2000

In [12]:
path='/Users/jpascual/Documents/Personal/Orga_datos_7506/TP2/tp2_orga_datos/events_up_to_01062018.csv'
path2='/Users/jpascual/Documents/Personal/Orga_datos_7506/events.csv'
labels='/Users/jpascual/Documents/Personal/Orga_datos_7506/TP2/tp2_orga_datos/labels_training_set.csv'

path_test='/Users/jpascual/Documents/Personal/Orga_datos_7506/trocafone_kaggle_test.csv'


In [13]:
# Lectura del dataframe:
df1=pd.read_csv(path)
#df1['origen']='new'
#df2=pd.read_csv(path2)
#df2['origen']='old'
#df=pd.concat([df1, df2])

df=df1

df_labels=pd.read_csv(labels)

df_test=pd.read_csv(path_test)
pd.options.display.max_columns = None

/Users/jpascual/Documents/Personal/anaconda/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (3,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [14]:
df.shape

(2341681, 23)

In [15]:
# Creo la columna timestamp en formato timestamp
df['timestamp2'] = pd.to_datetime(df['timestamp'])

# Re-ordeno el dataset
df=df.sort_values(by=['person','timestamp2']).reset_index()

In [16]:
# Columna timestamp del registro anterior
df['timestamp_anterior']=df['timestamp2'].shift()

# Armo el registro anterior de persona
df['persona_anterior']=df['person'].shift()

# Calculo la diferencia de tiempo
df.loc[df.event!='visited sit','time_diff']=df.timestamp2-df.timestamp_anterior

# Convierto la diferencia a minutos
df['tiempo_conv_mins'] = df['time_diff'].dt.total_seconds().div(60)

df['tiempo_conv_mins'] = df[df.person==df.persona_anterior].tiempo_conv_mins

# Creo dos datasets ya agrupados con el promedio y el maximo por persona. Después los joineo:
df_mean_time=df.groupby(['person']).agg({'tiempo_conv_mins':'mean'})
df_max_time=df.groupby(['person']).agg({'tiempo_conv_mins':'max'})

In [17]:
####################################################################################
# TRANSFORMACIONES Y CREACION DE VARIABLES NECESARIAS:

# Con esto creo un campo fecha:
df['fecha'] = pd.to_datetime(df['timestamp'], format='%Y-%m-%d').dt.date
df['fecha'] = df['fecha'].astype('datetime64[ns]')

# Columna número de mes
df['month']= pd.DatetimeIndex(df['timestamp']).month 
# Columna número de dia
df['day']= pd.DatetimeIndex(df['timestamp']).day 

# Columna con el nombre del mes
df.loc[df.month==1,'nombre_mes']='ENERO'
df.loc[df.month==2,'nombre_mes']='FEBRERO'
df.loc[df.month==3,'nombre_mes']='MARZO'
df.loc[df.month==4,'nombre_mes']='ABRIL'
df.loc[df.month==5,'nombre_mes']='MAYO'
df.loc[df.month==6,'nombre_mes']='JUNIO'
df.loc[df.month==7,'nombre_mes']='JULIO'
df.loc[df.month==8,'nombre_mes']='AGOSTO'
df.loc[df.month==9,'nombre_mes']='SEPTIEMBRE'


# Agrego dia de la semana y si es finde o no:
df['fecha2'] = df['fecha'].dt.dayofweek+1  # Sumo 1 para que no empiece en 0.

df.loc[df.fecha2==1,'dia'] ='LUNES'
df.loc[df.fecha2==2,'dia'] ='MARTES'
df.loc[df.fecha2==3,'dia'] ='MIERCOLES'
df.loc[df.fecha2==4,'dia'] ='JUEVES'
df.loc[df.fecha2==5,'dia'] ='VIERNES'
df.loc[df.fecha2==6,'dia'] ='SABADO'
df.loc[df.fecha2==7,'dia'] ='DOMINGO'


df.loc[df.fecha2==1,'lunes'] =1
df.loc[df.fecha2==2,'martes'] =1
df.loc[df.fecha2==3,'miercoles'] =1
df.loc[df.fecha2==4,'jueves'] =1
df.loc[df.fecha2==5,'viernes'] =1
df.loc[df.fecha2==6,'sabado'] =1
df.loc[df.fecha2==7,'domingo'] =1

# Definimos si es durante la semana o el finde:
df.loc[df.fecha2<=5,'week'] ='WEEK'
df.loc[df.fecha2>5,'week'] ='WEEKEND'

df.loc[df.fecha2<=5,'flag_week']=1
df.loc[df.fecha2>5,'flag_weekend']=1


# Armamos una columna con la MARCA del celu visto:
df.loc[(df['model'].str.lower().str.contains('iphone', na=False)==True),'brand_viewed']='IPHONE'
df.loc[(df['model'].str.lower().str.contains('samsung', na=False)==True)&(pd.isna(df.brand_viewed)),'brand_viewed']='SAMSUNG'
df.loc[(df['model'].str.lower().str.contains('motorola', na=False)==True)&(pd.isna(df.brand_viewed)),'brand_viewed']='MOTOROLA'
df.loc[(df['model'].str.lower().str.contains('sony', na=False)==True)&(pd.isna(df.brand_viewed)),'brand_viewed']='SONY'
df.loc[(df['model'].str.lower().str.contains('lg', na=False)==True)&(pd.isna(df.brand_viewed)),'brand_viewed']='LG'
df.loc[(df['model'].str.lower().str.contains('asus', na=False)==True)&(pd.isna(df.brand_viewed)),'brand_viewed']='ASUS'
df.loc[(df['model'].str.lower().str.contains('ipad', na=False)==True)&(pd.isna(df.brand_viewed)),'brand_viewed']='IPAD'
df.loc[(df['model'].str.lower().str.contains('lenovo', na=False)==True)&(pd.isna(df.brand_viewed)),'brand_viewed']='LENOVO'
df.loc[(df.event=='viewed product')&(pd.isna(df.brand_viewed)),'brand_viewed']='OTROS'


# Usuarios que convirtieron:
convirtieron=df[df.event=='conversion'].person.unique()

# Flag por tipo de evento:
df.loc[df.event=='visited site','visit']=1
df.loc[df.event=='viewed product','viewprod']=1
df.loc[df.event=='checkout','checkout']=1
df.loc[df.event=='brand listing','brand_listing']=1
df.loc[df.event=='ad campaign hit','ad_camp_hit']=1
df.loc[df.event=='generic listing','generic_listing']=1
df.loc[df.event=='searched products','searched_products']=1
df.loc[df.event=='search engine hit','search_engine_hit']=1
df.loc[df.event=='staticpage','staticpage']=1
df.loc[df.event=='conversion','conversion']=1
df.loc[df.event=='lead','lead']=1

# Modelo buscado:
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('iphone', na=False)==True),'searched_iphone']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('6s', na=False)==True),'searched_iphone_6s']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('7s', na=False)==True),'searched_iphone_7s']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('iphone 7', na=False)==True),'searched_iphone_7']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('iphone 6', na=False)==True),'searched_iphone_6']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('iphone 5', na=False)==True),'searched_iphone_5']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('samsung', na=False)==True),'searched_samsung']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('sony', na=False)==True),'searched_sony']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('xperia', na=False)==True),'searched_xperia']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('motorola', na=False)==True),'searched_motorola']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('a5', na=False)==True),'searched_a5']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('a7', na=False)==True),'searched_a7']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('j2', na=False)==True),'searched_j2']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('j3', na=False)==True),'searched_j3']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('j4', na=False)==True),'searched_j4']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('j5', na=False)==True),'searched_j5']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('j6', na=False)==True),'searched_j6']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('j7', na=False)==True),'searched_j7']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('s6', na=False)==True),'searched_s6']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('s7', na=False)==True),'searched_s7']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('s8', na=False)==True),'searched_s8']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('moto g', na=False)==True),'searched_moto_g']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('moto', na=False)==True),'searched_moto']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('galaxy', na=False)==True),'searched_galaxy']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('lg', na=False)==True),'searched_lg']=1
df.loc[(df.searched_products==1)&(df['search_term'].str.lower().str.contains('asus', na=False)==True),'searched_asus']=1




# Modelo visto:
df.loc[(df.brand_viewed=='IPHONE')&(df['model'].str.lower().str.contains('iphone se', na=False)==True),'iphone_se_viewed']=1
df.loc[(df.brand_viewed=='IPHONE')&(df['model'].str.lower().str.contains('iphone 5', na=False)==True),'iphone_5_viewed']=1
df.loc[(df.brand_viewed=='IPHONE')&(df['model'].str.lower().str.contains('iphone 6', na=False)==True),'iphone_6_viewed']=1
df.loc[(df.brand_viewed=='IPHONE')&(df['model'].str.lower().str.contains('iphone 7', na=False)==True),'iphone_7_viewed']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy s8 plus', na=False)==True),'samsung_s8_plus']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy s8', na=False)==True),'samsung_s8']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy s7', na=False)==True),'samsung_s7']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy s6', na=False)==True),'samsung_s6']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy s5', na=False)==True),'samsung_s5']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy s3', na=False)==True),'samsung_s5']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy s7 edge', na=False)==True),'samsung_s7_viewed']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy s6 edge', na=False)==True),'samsung_s6_viewed']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy note', na=False)==True),'samsung_note']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy note 8', na=False)==True),'samsung_note_8']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy a7', na=False)==True),'samsung_a7']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy a8', na=False)==True),'samsung_a8']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy a5', na=False)==True),'samsung_a5']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy j7', na=False)==True),'samsung_j7']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy j5', na=False)==True),'samsung_j5']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy j4', na=False)==True),'samsung_j4']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy j3', na=False)==True),'samsung_j3']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy j2', na=False)==True),'samsung_j2']=1
df.loc[(df.brand_viewed=='SAMSUNG')&(df['model'].str.lower().str.contains('galaxy j1', na=False)==True),'samsung_j1']=1
df.loc[(df.brand_viewed=='MOTOROLA')&(df['model'].str.lower().str.contains('moto g5', na=False)==True),'moto_g5']=1
df.loc[(df.brand_viewed=='MOTOROLA')&(df['model'].str.lower().str.contains('moto g4', na=False)==True),'moto_g4']=1
df.loc[(df.brand_viewed=='MOTOROLA')&(df['model'].str.lower().str.contains('moto g3', na=False)==True),'moto_g3']=1
df.loc[(df.brand_viewed=='MOTOROLA')&(df['model'].str.lower().str.contains('moto g2', na=False)==True),'moto_g2']=1
df.loc[(df.brand_viewed=='MOTOROLA')&(df['model'].str.lower().str.contains('moto g', na=False)==True),'moto_g']=1
df.loc[(df.brand_viewed=='MOTOROLA')&(df['model'].str.lower().str.contains('moto z', na=False)==True),'moto_z']=1
df.loc[(df.brand_viewed=='MOTOROLA')&(df['model'].str.lower().str.contains('x play', na=False)==True),'moto_x_play']=1
df.loc[(df.brand_viewed=='MOTOROLA')&(df['model'].str.lower().str.contains('moto x2', na=False)==True),'moto_x2']=1
df.loc[(df.brand_viewed=='MOTOROLA')&(df['model'].str.lower().str.contains('moto x', na=False)==True),'moto_x']=1
df.loc[(df.brand_viewed=='MOTOROLA')&(df['model'].str.lower().str.contains('moto e2', na=False)==True),'moto_e2']=1
df.loc[(df.brand_viewed=='SONY')&(df['model'].str.lower().str.contains('xperia m4', na=False)==True),'xperia_m4']=1
df.loc[(df.brand_viewed=='SONY')&(df['model'].str.lower().str.contains('xperia z', na=False)==True),'xperia_z']=1
df.loc[(df.brand_viewed=='SONY')&(df['model'].str.lower().str.contains('xperia z2', na=False)==True),'xperia_z2']=1
df.loc[(df.brand_viewed=='SONY')&(df['model'].str.lower().str.contains('xperia z3', na=False)==True),'xperia_z3']=1
df.loc[(df.brand_viewed=='SONY')&(df['model'].str.lower().str.contains('xperia z4', na=False)==True),'xperia_z4']=1
df.loc[(df.brand_viewed=='SONY')&(df['model'].str.lower().str.contains('xperia z5', na=False)==True),'xperia_z5']=1


# Modelo checkout:
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('iphone se', na=False)==True),'iphone_se_viewed_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('iphone 5', na=False)==True),'iphone_5_viewed_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('iphone 6', na=False)==True),'iphone_6_viewed_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('iphone 7', na=False)==True),'iphone_7_viewed_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy s8 plus', na=False)==True),'samsung_s8_plus_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy s8', na=False)==True),'samsung_s8_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy s7', na=False)==True),'samsung_s7_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy s6', na=False)==True),'samsung_s6_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy s5', na=False)==True),'samsung_s5_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy s3', na=False)==True),'samsung_s5_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy s7 edge', na=False)==True),'samsung_s7_viewed_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy s6 edge', na=False)==True),'samsung_s6_viewed_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy note', na=False)==True),'samsung_note_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy note 8', na=False)==True),'samsung_note_8_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy a7', na=False)==True),'samsung_a7_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy a8', na=False)==True),'samsung_a8_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy a5', na=False)==True),'samsung_a5_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy j7', na=False)==True),'samsung_j7_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy j5', na=False)==True),'samsung_j5_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy j4', na=False)==True),'samsung_j4_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy j3', na=False)==True),'samsung_j3_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy j2', na=False)==True),'samsung_j2_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('galaxy j1', na=False)==True),'samsung_j1_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('moto g5', na=False)==True),'moto_g5_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('moto g4', na=False)==True),'moto_g4_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('moto g3', na=False)==True),'moto_g3_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('moto g2', na=False)==True),'moto_g2_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('moto g', na=False)==True),'moto_g_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('moto z', na=False)==True),'moto_z_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('x play', na=False)==True),'moto_x_play_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('moto x2', na=False)==True),'moto_x2_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('moto x', na=False)==True),'moto_x_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('moto e2', na=False)==True),'moto_e2_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('xperia m4', na=False)==True),'xperia_m4_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('xperia z', na=False)==True),'xperia_z_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('xperia z2', na=False)==True),'xperia_z2_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('xperia z3', na=False)==True),'xperia_z3_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('xperia z4', na=False)==True),'xperia_z4_cho']=1
df.loc[(df.checkout==1)&(df['model'].str.lower().str.contains('xperia z5', na=False)==True),'xperia_z5_cho']=1


# Modelo conversion:
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('iphone se', na=False)==True),'iphone_se_viewed_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('iphone 5', na=False)==True),'iphone_5_viewed_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('iphone 6', na=False)==True),'iphone_6_viewed_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('iphone 7', na=False)==True),'iphone_7_viewed_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy s8 plus', na=False)==True),'samsung_s8_plus_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy s8', na=False)==True),'samsung_s8_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy s7', na=False)==True),'samsung_s7_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy s6', na=False)==True),'samsung_s6_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy s5', na=False)==True),'samsung_s5_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy s3', na=False)==True),'samsung_s5_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy s7 edge', na=False)==True),'samsung_s7_viewed_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy s6 edge', na=False)==True),'samsung_s6_viewed_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy note', na=False)==True),'samsung_note_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy note 8', na=False)==True),'samsung_note_8_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy a7', na=False)==True),'samsung_a7_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy a8', na=False)==True),'samsung_a8_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy a5', na=False)==True),'samsung_a5_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy j7', na=False)==True),'samsung_j7_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy j5', na=False)==True),'samsung_j5_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy j4', na=False)==True),'samsung_j4_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy j3', na=False)==True),'samsung_j3_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy j2', na=False)==True),'samsung_j2_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('galaxy j1', na=False)==True),'samsung_j1_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('moto g5', na=False)==True),'moto_g5_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('moto g4', na=False)==True),'moto_g4_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('moto g3', na=False)==True),'moto_g3_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('moto g2', na=False)==True),'moto_g2_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('moto g', na=False)==True),'moto_g_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('moto z', na=False)==True),'moto_z_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('x play', na=False)==True),'moto_x_play_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('moto x2', na=False)==True),'moto_x2_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('moto x', na=False)==True),'moto_x_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('moto e2', na=False)==True),'moto_e2_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('xperia m4', na=False)==True),'xperia_m4_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('xperia z', na=False)==True),'xperia_z_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('xperia z2', na=False)==True),'xperia_z2_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('xperia z3', na=False)==True),'xperia_z3_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('xperia z4', na=False)==True),'xperia_z4_conv']=1
df.loc[(df.conversion==1)&(df['model'].str.lower().str.contains('xperia z5', na=False)==True),'xperia_z5_conv']=1


# condition:
df.loc[(df['condition'].str.lower().str.contains('bom', na=False)==True),'condition_bom']=1
df.loc[(df['condition'].str.lower().str.contains('excelente', na=False)==True),'condition_excelente']=1
df.loc[(df['condition'].str.lower().str.contains('muito', na=False)==True),'condition_muito_bom']=1
df.loc[(df['condition'].str.lower().str.contains('touch', na=False)==True),'condition_touch']=1
df.loc[(df['condition'].str.lower().str.contains('novo', na=False)==True),'condition_novo']=1

df.loc[(df.checkout==1)&(df['condition'].str.lower().str.contains('bom', na=False)==True),'condition_bom_cho']=1
df.loc[(df.checkout==1)&(df['condition'].str.lower().str.contains('excelente', na=False)==True),'condition_excelente_cho']=1
df.loc[(df.checkout==1)&(df['condition'].str.lower().str.contains('muito', na=False)==True),'condition_muito_bom_cho']=1
df.loc[(df.checkout==1)&(df['condition'].str.lower().str.contains('touch', na=False)==True),'condition_touch_cho']=1
df.loc[(df.checkout==1)&(df['condition'].str.lower().str.contains('novo', na=False)==True),'condition_novo_cho']=1

df.loc[(df.conversion==1)&(df['condition'].str.lower().str.contains('bom', na=False)==True),'condition_bom_conv']=1
df.loc[(df.conversion==1)&(df['condition'].str.lower().str.contains('excelente', na=False)==True),'condition_excelente_conv']=1
df.loc[(df.conversion==1)&(df['condition'].str.lower().str.contains('muito', na=False)==True),'condition_muito_bom_conv']=1
df.loc[(df.conversion==1)&(df['condition'].str.lower().str.contains('touch', na=False)==True),'condition_touch_conv']=1
df.loc[(df.conversion==1)&(df['condition'].str.lower().str.contains('novo', na=False)==True),'condition_novo_conv']=1




# Search engine hit:
df.loc[(df.search_engine_hit==1)&(df['search_engine'].str.lower().str.contains('google', na=False)==True),'searched_google']=1
df.loc[(df.search_engine_hit==1)&(df['search_engine'].str.lower().str.contains('bing', na=False)==True),'searched_bing']=1
df.loc[(df.search_engine_hit==1)&(df['search_engine'].str.lower().str.contains('yahoo', na=False)==True),'searched_yahoo']=1


####################################################################################



df.sample(100)

index            timestamp              event    person  \
2011187  1145995  2018-05-23 17:01:35     viewed product  dd298c63   
124398   1188373  2018-05-23 12:54:46     viewed product  0d43b999   
1865169  1160034  2018-05-29 11:01:45     viewed product  ccef1c9f   
1607913  1237484  2018-05-30 17:29:03     viewed product  b0967571   
1556109  1712522  2018-03-31 18:19:16    ad campaign hit  aa85f45e   
794979     74796  2018-05-28 13:33:46     viewed product  55fc24ef   
764902    931553  2018-05-28 23:32:44    ad campaign hit  52f4226f   
1514546   349531  2018-04-04 17:55:24     viewed product  a5e456ab   
1333805   556775  2018-05-18 17:35:43     viewed product  92474d59   
503079   1035515  2018-04-24 21:28:43     viewed product  36c224c9   
116265   1377504  2018-04-02 20:13:40     viewed product  0c285c5b   
1294180   487364  2018-05-24 14:44:35     viewed product  8e3b328e   
2327606  1472253  2018-05-21 19:18:12    ad campaign hit  fee8d0fe   
1949414   181006  2018-05-23 12:28:21  search engine hit  d6b69511   
920963   1855025  2018-05-01 22:10:47    generic listing  64346005   
17094    1771511  2018-05-28 15:33:09      brand listing  01f20b0a   
2018622   771123  2018-05-01 15:48:47     viewed product  ddb4d062   
1766238  1933268  2018-05-13 14:16:54      brand listing  c288a0dc   
1082830  1139509  2018-05-18 15:48:44     viewed product  7549f65a   
2085714  2105335  2018-04-15 04:49:33    generic listing  e4418de8   
1525509   584521  2018-05-13 20:24:06  search engine hit  a7561f58   
1871525  1442822  2018-05-20 16:57:46     viewed product  cdaa445c   
1141553  1144025  2018-05-23 17:31:40     viewed product  7c04cb42   
1304474   612537  2018-05-17 01:08:25     viewed product  8f3fc2c1   
852032    322161  2018-04-05 15:30:02  search engine hit  5bfbd742   
2074672   665518  2018-05-02 23:38:22     viewed product  e33c3912   
326531   2106581  2018-05-27 22:21:43      brand listing  22cab523   
73631    2134627  2018-05-27 17:18:57    generic listing  07fef028   
2309496   737326  2018-05-21 13:40:47  searched products  fcc93318   
1190981  1525854  2018-05-18 19:56:39     viewed product  8219bd4d   
1386136   890808  2018-05-26 22:40:55     viewed product  988006ff   
274668    292689  2018-04-17 18:47:42     viewed product  1cdb7e7d   
2134866  1364391  2018-04-24 16:10:51     viewed product  e9890772   
1145037  1202649  2018-05-16 23:21:00     viewed product  7c93931b   
1137662  1295940  2018-05-28 22:20:30     viewed product  7b8d2af8   
837152    451948  2018-05-19 22:29:32  searched products  5a47f7c9   
1527761  1512976  2018-05-25 12:01:30     viewed product  a7937ad1   
1383670   565097  2018-05-30 20:19:42     viewed product  9822a024   
1001626   167818  2018-05-22 10:47:29     viewed product  6bd1ecd3   
929613    319884  2018-03-26 21:38:37    ad campaign hit  652f2bd2   
2109286  1803570  2018-05-19 00:26:00    generic listing  e6b64ddd   
1888989   638419  2018-04-04 21:11:43     viewed product  cfe46fe7   
1460588   453782  2018-05-19 12:35:12    ad campaign hit  9fd7ee44   
443725   1271614  2018-05-20 02:22:23     viewed product  30235fef   
776912    999195  2018-03-27 20:00:15  searched products  542336f4   
641080    712073  2018-02-11 20:49:24  search engine hit  44f60b8d   
430681   2217714  2018-05-22 09:42:37       visited site  2efc74ac   
1620336   647755  2018-04-05 02:32:04     viewed product  b1f4dbf6   
1827270   721071  2018-01-20 11:21:09     viewed product  c8aebe6d   
745871    501003  2018-05-31 01:25:26     viewed product  50caa16d   
1180691   605861  2018-04-27 22:58:41     viewed product  810b7128   
396623    594382  2018-05-15 19:08:57           checkout  2a9334fb   
878681   1136932  2018-05-18 02:42:55     viewed product  5f1ea57c   
1280955  1758933  2018-03-15 14:52:26     viewed product  8cdb5260   
1769184  2199835  2018-05-23 02:59:44       visited site  c3058a76   
712094   2030966  2018-05-01 17:58:47      brand listing  4d06389d   
1049630   216364  201

In [18]:
# Armamos una columna con la MARCA del celu visto:
df.loc[(df['model'].str.lower().str.contains('iphone', na=False)==True),'iphone_viewed']=1
df.loc[(df['model'].str.lower().str.contains('samsung', na=False)==True),'samsung_viewed']=1
df.loc[(df['model'].str.lower().str.contains('motorola', na=False)==True),'motorola_viewed']=1
df.loc[(df['model'].str.lower().str.contains('sony', na=False)==True),'sony_viewed']=1
df.loc[(df['model'].str.lower().str.contains('lg', na=False)==True),'lg_viewed']=1
df.loc[(df['model'].str.lower().str.contains('asus', na=False)==True),'asus_viewed']=1
df.loc[(df['model'].str.lower().str.contains('ipad', na=False)==True),'ipad_viewed']=1




# flag storage
df.loc[df['storage']=='8GB','storage_8']=1
df.loc[df['storage']=='16GB','storage_16']=1
df.loc[df['storage']=='32GB','storage_32']=1
df.loc[df['storage']=='64GB','storage_64']=1
df.loc[df['storage']=='128GB','storage_128']=1
df.loc[df['storage']=='4GB','storage_4']=1
df.loc[df['storage']=='256GB','storage_256']=1
df.loc[df['storage']=='512MB','storage_512MB']=1


# variables referentes a la visita:
df.loc[df.event=='visited site','visit']=1
df.loc[(df.event=='visited site')&(df.nombre_mes=='MAYO'),'visit_mayo']=1
df.loc[(df.event=='visited site')&(df.nombre_mes=='ABRIL'),'visit_abril']=1
df.loc[(df.event=='visited site')&(df.nombre_mes=='MARZO'),'visit_marzo']=1
df.loc[(df.event=='visited site')&(df.nombre_mes=='FEBRERO'),'visit_febrero']=1
df.loc[(df.event=='visited site')&(df.nombre_mes=='ENERO'),'visit_enero']=1


# variables referentes a la conversión:
df.loc[df.event=='conversion','conversion']=1
df.loc[(df.event=='conversion')&(df.nombre_mes=='MAYO'),'conv_mayo']=1
df.loc[(df.event=='conversion')&(df.nombre_mes=='ABRIL'),'conv_abril']=1
df.loc[(df.event=='conversion')&(df.nombre_mes=='MARZO'),'conv_marzo']=1
df.loc[(df.event=='conversion')&(df.nombre_mes=='FEBRERO'),'conv_febrero']=1
df.loc[(df.event=='conversion')&(df.nombre_mes=='ENERO'),'conv_enero']=1

# indica si buscó algo en el buscador:
df.loc[df.search_term.notnull() ,'busqueda_term']=1


# Operating system
df.loc[(df['operating_system_version'].str.lower().str.contains('windows', na=False)==True),'sist_oper_windows']=1
df.loc[(df['operating_system_version'].str.lower().str.contains('android', na=False)==True),'sist_oper_android']=1
df.loc[(df['operating_system_version'].str.lower().str.contains('ios', na=False)==True),'sist_oper_ios']=1
df.loc[(df['operating_system_version'].str.lower().str.contains('mac', na=False)==True),'sist_oper_mac']=1
df.loc[(df['operating_system_version'].str.lower().str.contains('linux', na=False)==True),'sist_oper_linux']=1

# Flag color
df.loc[(df['color'].str.lower().str.contains('preto', na=False)==True),'col_preto']=1
df.loc[(df['color'].str.lower().str.contains('dourado', na=False)==True),'col_dourado']=1
df.loc[(df['color'].str.lower().str.contains('cinza', na=False)==True),'col_cinza']=1
df.loc[(df['color'].str.lower().str.contains('branco', na=False)==True),'col_branco']=1
df.loc[(df['color'].str.lower().str.contains('prateado', na=False)==True),'col_prateado']=1
df.loc[(df['color'].str.lower().str.contains('rosa', na=False)==True),'col_rosa']=1

#Flag campaign_source
df.loc[(df['campaign_source'].str.lower().str.contains('google', na=False)==True),'camp_google']=1
df.loc[(df['campaign_source'].str.lower().str.contains('criteo', na=False)==True),'camp_criteo']=1
df.loc[(df['campaign_source'].str.lower().str.contains('rtbhouse', na=False)==True),'camp_rtbhouse']=1
df.loc[(df['campaign_source'].str.lower().str.contains('zanox', na=False)==True),'camp_zanox']=1

# Flags de checkout por mes
df.loc[(df.event=='checkout')&(df.nombre_mes=='MAYO'),'CHO_MAYO']=1
df.loc[(df.event=='checkout')&(df.nombre_mes=='ABRIL'),'CHO_ABRIL']=1
df.loc[(df.event=='checkout')&(df.nombre_mes=='MARZO'),'CHO_MARZO']=1
df.loc[(df.event=='checkout')&(df.nombre_mes=='FEBRERO'),'CHO_FEBRERO']=1
df.loc[(df.event=='checkout')&(df.nombre_mes=='ENERO'),'CHO_ENERO']=1



#Flag channel
df.loc[(df['channel'].str.lower().str.contains('paid', na=False)==True),'chan_paid']=1
df.loc[(df['channel'].str.lower().str.contains('direct', na=False)==True),'chan_direct']=1
df.loc[(df['channel'].str.lower().str.contains('referral', na=False)==True),'chan_referral']=1
df.loc[(df['channel'].str.lower().str.contains('organic', na=False)==True),'chan_organic']=1

#Flag New vs Returning

df.loc[(df['new_vs_returning'].str.lower().str.contains('returning', na=False)==True),'nvsr_return']=1
df.loc[(df['new_vs_returning'].str.lower().str.contains('new', na=False)==True),'nvsr_new']=1

#Flag Ciudad

df.loc[(df['city'].str.lower().str.contains('são paulo', na=False)==True),'city_saopaulo']=1
df.loc[(df['city'].str.lower().str.contains('rio de janeiro', na=False)==True),'city_rio']=1
df.loc[(df['city'].str.lower().str.contains('belo horizonte', na=False)==True),'city_belo']=1
df.loc[(df['city'].str.lower().str.contains('salvador', na=False)==True),'city_salv']=1


#Flag dispositivo
df.loc[(df['device_type'].str.lower().str.contains('smartphone', na=False)==True),'disp_smart']=1
df.loc[(df['device_type'].str.lower().str.contains('computer', na=False)==True),'disp_comp']=1
df.loc[(df['device_type'].str.lower().str.contains('tablet', na=False)==True),'disp_tablet']=1


#Flag resolución
df.loc[(df['screen_resolution'].str.lower().str.contains('360x640', na=False)==True),'res_360x640']=1
df.loc[(df['screen_resolution'].str.lower().str.contains('1366x768', na=False)==True),'res_1366x768']=1
df.loc[(df['screen_resolution'].str.lower().str.contains('1920x1080', na=False)==True),'res_1920x1080']=1


In [19]:
# semanas de mayo:
df.loc[(df['day']<=7) & (df['month']==5),'Primera_Semana']=1
df.loc[(df['day']>7) & (df['day']<=15) & (df['month']==5) ,'Segunda_Semana']=1
df.loc[(df['day']>15) &(df['day']<=21) & (df['month']==5),'Tercera_Semana']=1
df.loc[(df['day']>21) &(df['day']<=28) & (df['month']==5),'Cuarta_Semana']=1
df.loc[(df['day']>28) & (df['month']==5),'Fin_de_Mes']=1

# semanas y productos:
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('iphone', na=False)==True),'iphone_1eraSem']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('iphone', na=False)==True),'iphone_2daSem']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('iphone', na=False)==True),'iphone_3eraSem']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('iphone', na=False)==True),'iphone_4taSem']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('iphone', na=False)==True),'iphone_FindeMes']=1

df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('samsung', na=False)==True),'samsung_1eraSem']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('samsung', na=False)==True),'samsung_2daSem']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('samsung', na=False)==True),'samsung_3eraSem']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('samsung', na=False)==True),'samsung_4taSem']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('samsung', na=False)==True),'samsung_FindeMes']=1

df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('motorola', na=False)==True),'motorola_1eraSem']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('motorola', na=False)==True),'motorola_2daSem']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('motorola', na=False)==True),'motorola_3eraSem']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('motorola', na=False)==True),'motorola_4taSem']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('motorola', na=False)==True),'motorola_FindeMes']=1

df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('', na=False)==True),'motorola_1eraSem']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('motorola', na=False)==True),'motorola_2daSem']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('motorola', na=False)==True),'motorola_3eraSem']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('motorola', na=False)==True),'motorola_4taSem']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('motorola', na=False)==True),'motorola_FindeMes']=1


df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('iphone se', na=False)==True),'Iphonese_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('iphone 5', na=False)==True),'Iphone5_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('iphone 6', na=False)==True),'Iphone6_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('iphone 7', na=False)==True),'Iphone7_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy s8 plus', na=False)==True),'galaxy_s8_plus_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy s8', na=False)==True),'galaxy_s8_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy s7', na=False)==True),'galaxy_s7_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy s6', na=False)==True),'galaxy_s6_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy s5', na=False)==True),'galaxy_s5_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy s3', na=False)==True),'galaxy_s3_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy s7 edge', na=False)==True),'galaxy_s7_edge_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy s6 edge', na=False)==True),'galaxy_s6_edge_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy note', na=False)==True),'galaxy_note_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy a7', na=False)==True),'galaxy_a7_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy a8', na=False)==True),'galaxy_a8_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy a5', na=False)==True),'galaxy_a5_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy j7', na=False)==True),'galaxy_j7_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy j5', na=False)==True),'galaxy_j5_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy j4', na=False)==True),'galaxy_j4_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy j3', na=False)==True),'galaxy_j3_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy j2', na=False)==True),'galaxy_j2_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('galaxy j1', na=False)==True),'galaxy_j1_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('moto g5', na=False)==True),'moto_g5_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('moto g4', na=False)==True),'moto_g4_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('moto g3', na=False)==True),'moto_g3_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('moto g2', na=False)==True),'moto_g2_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('moto g', na=False)==True),'moto_g_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('moto z', na=False)==True),'moto_z_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('x play', na=False)==True),'xplay_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('moto x2', na=False)==True),'moto_x2_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('moto x', na=False)==True),'moto_x_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('moto e2', na=False)==True),'moto_e2_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('xperia m4', na=False)==True),'xperia_m4_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('xperia z', na=False)==True),'xperia_z_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('xperia z2', na=False)==True),'xperia_z2_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('xperia z3', na=False)==True),'xperia_z3_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('xperia z4', na=False)==True),'xperia_z4_FindeMes']=1
df.loc[(df.Fin_de_Mes==1)&(df['model'].str.lower().str.contains('xperia z5', na=False)==True),'xperia_z5_FindeMes']=1

df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('iphone se', na=False)==True),'Iphonese_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('iphone 5', na=False)==True),'Iphone5_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('iphone 6', na=False)==True),'Iphone6_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('iphone 7', na=False)==True),'Iphone7_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy s8 plus', na=False)==True),'galaxy_s8_plus_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy s8', na=False)==True),'galaxy_s8_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy s7', na=False)==True),'galaxy_s7_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy s6', na=False)==True),'galaxy_s6_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy s5', na=False)==True),'galaxy_s5_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy s3', na=False)==True),'galaxy_s3_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy s7 edge', na=False)==True),'galaxy_s7_edge_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy s6 edge', na=False)==True),'galaxy_s6_edge_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy note', na=False)==True),'galaxy_note_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy a7', na=False)==True),'galaxy_a7_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy a8', na=False)==True),'galaxy_a8_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy a5', na=False)==True),'galaxy_a5_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy j7', na=False)==True),'galaxy_j7_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy j5', na=False)==True),'galaxy_j5_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy j4', na=False)==True),'galaxy_j4_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy j3', na=False)==True),'galaxy_j3_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy j2', na=False)==True),'galaxy_j2_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('galaxy j1', na=False)==True),'galaxy_j1_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('moto g5', na=False)==True),'moto_g5_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('moto g4', na=False)==True),'moto_g4_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('moto g3', na=False)==True),'moto_g3_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('moto g2', na=False)==True),'moto_g2_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('moto g', na=False)==True),'moto_g_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('moto z', na=False)==True),'moto_z_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('x play', na=False)==True),'xplay_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('moto x2', na=False)==True),'moto_x2_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('moto x', na=False)==True),'moto_x_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('moto e2', na=False)==True),'moto_e2_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('xperia m4', na=False)==True),'xperia_m4_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('xperia z', na=False)==True),'xperia_z_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('xperia z2', na=False)==True),'xperia_z2_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('xperia z3', na=False)==True),'xperia_z3_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('xperia z4', na=False)==True),'xperia_z4_1eraSemana']=1
df.loc[(df.Primera_Semana==1)&(df['model'].str.lower().str.contains('xperia z5', na=False)==True),'xperia_z5_1eraSemana']=1

df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('iphone se', na=False)==True),'Iphonese_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('iphone 5', na=False)==True),'Iphone5_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('iphone 6', na=False)==True),'Iphone6_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('iphone 7', na=False)==True),'Iphone7_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy s8 plus', na=False)==True),'galaxy_s8_plus_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy s8', na=False)==True),'galaxy_s8_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy s7', na=False)==True),'galaxy_s7_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy s6', na=False)==True),'galaxy_s6_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy s5', na=False)==True),'galaxy_s5_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy s3', na=False)==True),'galaxy_s3_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy s7 edge', na=False)==True),'galaxy_s7_edge_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy s6 edge', na=False)==True),'galaxy_s6_edge_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy note', na=False)==True),'galaxy_note_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy a7', na=False)==True),'galaxy_a7_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy a8', na=False)==True),'galaxy_a8_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy a5', na=False)==True),'galaxy_a5_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy j7', na=False)==True),'galaxy_j7_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy j5', na=False)==True),'galaxy_j5_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy j4', na=False)==True),'galaxy_j4_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy j3', na=False)==True),'galaxy_j3_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy j2', na=False)==True),'galaxy_j2_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('galaxy j1', na=False)==True),'galaxy_j1_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('moto g5', na=False)==True),'moto_g5_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('moto g4', na=False)==True),'moto_g4_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('moto g3', na=False)==True),'moto_g3_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('moto g2', na=False)==True),'moto_g2_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('moto g', na=False)==True),'moto_g_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('moto z', na=False)==True),'moto_z_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('x play', na=False)==True),'xplay_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('moto x2', na=False)==True),'moto_x2_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('moto x', na=False)==True),'moto_x_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('moto e2', na=False)==True),'moto_e2_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('xperia m4', na=False)==True),'xperia_m4_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('xperia z', na=False)==True),'xperia_z_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('xperia z2', na=False)==True),'xperia_z2_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('xperia z3', na=False)==True),'xperia_z3_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('xperia z4', na=False)==True),'xperia_z4_2daSemana']=1
df.loc[(df.Segunda_Semana==1)&(df['model'].str.lower().str.contains('xperia z5', na=False)==True),'xperia_z5_2daSemana']=1

df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('iphone se', na=False)==True),'Iphonese_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('iphone 5', na=False)==True),'Iphone5_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('iphone 6', na=False)==True),'Iphone6_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('iphone 7', na=False)==True),'Iphone7_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy s8 plus', na=False)==True),'galaxy_s8_plus_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy s8', na=False)==True),'galaxy_s8_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy s7', na=False)==True),'galaxy_s7_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy s6', na=False)==True),'galaxy_s6_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy s5', na=False)==True),'galaxy_s5_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy s3', na=False)==True),'galaxy_s3_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy s7 edge', na=False)==True),'galaxy_s7_edge_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy s6 edge', na=False)==True),'galaxy_s6_edge_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy note', na=False)==True),'galaxy_note_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy a7', na=False)==True),'galaxy_a7_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy a8', na=False)==True),'galaxy_a8_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy a5', na=False)==True),'galaxy_a5_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy j7', na=False)==True),'galaxy_j7_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy j5', na=False)==True),'galaxy_j5_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy j4', na=False)==True),'galaxy_j4_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy j3', na=False)==True),'galaxy_j3_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy j2', na=False)==True),'galaxy_j2_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('galaxy j1', na=False)==True),'galaxy_j1_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('moto g5', na=False)==True),'moto_g5_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('moto g4', na=False)==True),'moto_g4_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('moto g3', na=False)==True),'moto_g3_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('moto g2', na=False)==True),'moto_g2_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('moto g', na=False)==True),'moto_g_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('moto z', na=False)==True),'moto_z_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('x play', na=False)==True),'xplay_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('moto x2', na=False)==True),'moto_x2_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('moto x', na=False)==True),'moto_x_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('moto e2', na=False)==True),'moto_e2_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('xperia m4', na=False)==True),'xperia_m4_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('xperia z', na=False)==True),'xperia_z_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('xperia z2', na=False)==True),'xperia_z2_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('xperia z3', na=False)==True),'xperia_z3_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('xperia z4', na=False)==True),'xperia_z4_3eraSemana']=1
df.loc[(df.Tercera_Semana==1)&(df['model'].str.lower().str.contains('xperia z5', na=False)==True),'xperia_z5_3eraSemana']=1

df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('iphone se', na=False)==True),'Iphonese_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('iphone 5', na=False)==True),'Iphone5_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('iphone 6', na=False)==True),'Iphone6_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('iphone 7', na=False)==True),'Iphone7_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy s8 plus', na=False)==True),'galaxy_s8_plus_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy s8', na=False)==True),'galaxy_s8_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy s7', na=False)==True),'galaxy_s7_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy s6', na=False)==True),'galaxy_s6_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy s5', na=False)==True),'galaxy_s5_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy s3', na=False)==True),'galaxy_s3_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy s7 edge', na=False)==True),'galaxy_s7_edge_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy s6 edge', na=False)==True),'galaxy_s6_edge_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy note', na=False)==True),'galaxy_note_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy a7', na=False)==True),'galaxy_a7_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy a8', na=False)==True),'galaxy_a8_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy a5', na=False)==True),'galaxy_a5_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy j7', na=False)==True),'galaxy_j7_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy j5', na=False)==True),'galaxy_j5_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy j4', na=False)==True),'galaxy_j4_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy j3', na=False)==True),'galaxy_j3_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy j2', na=False)==True),'galaxy_j2_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('galaxy j1', na=False)==True),'galaxy_j1_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('moto g5', na=False)==True),'moto_g5_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('moto g4', na=False)==True),'moto_g4_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('moto g3', na=False)==True),'moto_g3_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('moto g2', na=False)==True),'moto_g2_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('moto g', na=False)==True),'moto_g_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('moto z', na=False)==True),'moto_z_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('x play', na=False)==True),'xplay_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('moto x2', na=False)==True),'moto_x2_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('moto x', na=False)==True),'moto_x_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('moto e2', na=False)==True),'moto_e2_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('xperia m4', na=False)==True),'xperia_m4_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('xperia z', na=False)==True),'xperia_z_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('xperia z2', na=False)==True),'xperia_z2_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('xperia z3', na=False)==True),'xperia_z3_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('xperia z4', na=False)==True),'xperia_z4_4taSemana']=1
df.loc[(df.Cuarta_Semana==1)&(df['model'].str.lower().str.contains('xperia z5', na=False)==True),'xperia_z5_4taSemana']=1



#Flag campaign_source

df.loc[(df['campaign_source'].str.lower().str.contains('google', na=False)==True),'camp']='GOOGLE'
df.loc[(df['campaign_source'].str.lower().str.contains('criteo', na=False)==True),'camp']='CRITEO'
df.loc[(df['campaign_source'].str.lower().str.contains('rtbhouse', na=False)==True),'camp']='RTBHOUSE'
df.loc[(df['campaign_source'].str.lower().str.contains('zanox', na=False)==True),'camp']='ZANOX'
df.loc[(df['campaign_source'].str.lower().str.contains('emblue', na=False)==True),'camp']='EMBLUE'
df.loc[(df['campaign_source'].str.lower().str.contains('afilio', na=False)==True),'camp']='AFILIO'
df.loc[(df['campaign_source'].str.lower().str.contains('manifest', na=False)==True),'camp']='MANIFEST'
df.loc[(df['campaign_source'].str.lower().str.contains('facebookads', na=False)==True),'camp']='FACEBOOKADS'
df.loc[(df['campaign_source'].str.lower().str.contains('voxus', na=False)==True),'camp']='VOXUS'
df.loc[(df['campaign_source'].str.lower().str.contains('rakuten', na=False)==True),'camp']='RAKUTEN'
df.loc[(df['campaign_source'].str.lower().str.contains('bing', na=False)==True),'camp']='BING'
df.loc[(df['campaign_source'].str.lower().str.contains('datacrush', na=False)==True),'camp']='DATACRUSH'
df.loc[(df['campaign_source'].str.lower().str.contains('indexa', na=False)==True),'camp']='INDEXA'
df.loc[(df['campaign_source'].str.lower().str.contains('buscape', na=False)==True),'camp']='BUSCAPE'
df.loc[(df['campaign_source'].str.lower().str.contains('facebook', na=False)==True),'camp']='FACEBOOK'
df.loc[(df['campaign_source'].str.lower().str.contains('afiliado', na=False)==True),'camp']='AFILIADO'
df.loc[(df['event']== 'ad campaign hit')&(pd.isna(df.camp)),'camp']='OTROS'

df.loc[(df['camp'].str.lower().str.contains('google', na=False)==True),'camp_google']=1
df.loc[(df['camp'].str.lower().str.contains('criteo', na=False)==True),'camp_criteo']=1
df.loc[(df['camp'].str.lower().str.contains('rtbhouse', na=False)==True),'camp_rtbhouse']=1
df.loc[(df['camp'].str.lower().str.contains('zanox', na=False)==True),'camp_zanox']=1
df.loc[(df['camp'].str.lower().str.contains('emblue', na=False)==True),'camp_emblue']=1
df.loc[(df['camp'].str.lower().str.contains('afilio', na=False)==True),'camp_afilio']=1
df.loc[(df['camp'].str.lower().str.contains('manifest', na=False)==True),'camp_manifest']=1
df.loc[(df['camp'].str.lower().str.contains('facebookads', na=False)==True),'camp_facebookads']=1
df.loc[(df['camp'].str.lower().str.contains('voxus', na=False)==True),'camp_voxus']=1
df.loc[(df['camp'].str.lower().str.contains('rakuten', na=False)==True),'camp_rakuten']=1
df.loc[(df['camp'].str.lower().str.contains('bing', na=False)==True),'camp_bing']=1
df.loc[(df['camp'].str.lower().str.contains('datacrush', na=False)==True),'camp_datacrush']=1
df.loc[(df['camp'].str.lower().str.contains('indexa', na=False)==True),'camp_indexa']=1
df.loc[(df['camp'].str.lower().str.contains('buscape', na=False)==True),'camp_buscape']=1
df.loc[(df['camp'].str.lower().str.contains('facebook', na=False)==True),'camp_facebook']=1
df.loc[(df['camp'].str.lower().str.contains('afiliado', na=False)==True),'camp_afiliado']=1
df.loc[(df['camp'].str.lower().str.contains('otros', na=False)==True),'camp_otros']=1




## Flag por URL
#Flag de Url por marca
df.loc[(df['url'].str.lower().str.contains('comprar', na=False)==True),'url_comprar']=1
df.loc[(df['url'].str.lower().str.contains('vender', na=False)==True),'url_vender']=1
df.loc[(df['url'].str.lower().str.contains('iphone', na=False)==True),'url_iphone']=1
df.loc[(df['url'].str.lower().str.contains('samsung', na=False)==True),'url_samsung']=1
df.loc[(df['url'].str.lower().str.contains('motorola', na=False)==True),'url_motorola']=1
df.loc[(df['url'].str.lower().str.contains('lg', na=False)==True),'url_lg']=1
df.loc[(df['url'].str.lower().str.contains('ipad', na=False)==True),'url_ipad']=1
df.loc[(df['url'].str.lower().str.contains('asus', na=False)==True),'url_asus']=1
df.loc[(df['url'].str.lower().str.contains('apple', na=False)==True),'url_apple']=1
df.loc[(df['url'].str.lower().str.contains('sony', na=False)==True),'url_sony']=1
df.loc[(df['url'].str.lower().str.contains('quantum', na=False)==True),'url_quantum']=1

#Flag de Url por marca
df.loc[(df['url'].str.lower().str.contains('6s', na=False)==True),'url_6s']=1
df.loc[(df['url'].str.lower().str.contains('6', na=False)==True),'url_6']=1
df.loc[(df['url'].str.lower().str.contains('iphone-5s', na=False)==True),'url_iphone-5s']=1
df.loc[(df['url'].str.lower().str.contains('galaxy', na=False)==True),'url_galaxy']=1
df.loc[(df['url'].str.lower().str.contains('galaxy-j5', na=False)==True),'url_galaxy-j5']=1
df.loc[(df['url'].str.lower().str.contains('galaxy-s7', na=False)==True),'galaxy-s7']=1
df.loc[(df['url'].str.lower().str.contains('galaxy-s6', na=False)==True),'url_galaxy-s6']=1
df.loc[(df['url'].str.lower().str.contains('galaxy-j7', na=False)==True),'url_galaxy-j7']=1
df.loc[(df['url'].str.lower().str.contains('galaxy-s8', na=False)==True),'url_galaxy-s8']=1


In [28]:
df.sample(500)

index            timestamp              event    person  \
896166    824133  2018-05-25 13:45:06     viewed product  618b2d0f   
894436   2208354  2018-05-26 18:01:34       visited site  613c97af   
2069831   748506  2018-05-06 16:52:36     viewed product  e2bce12f   
1500986   515822  2018-05-17 23:53:03  search engine hit  a4507ea0   
1981859   511282  2018-05-19 02:53:53     viewed product  d99db92d   
131118    276047  2018-05-14 11:11:55     viewed product  0dbcf50c   
235146    194437  2018-05-24 20:59:00     viewed product  18489dd5   
1654398  1255637  2018-05-22 21:10:03     viewed product  b5c388b4   
1238266   201352  2018-05-10 13:55:27  searched products  8808e6a9   
1142757  1365790  2018-04-22 23:56:11     viewed product  7c250435   
1547490   450121  2018-05-19 14:25:30  searched products  a96e4d07   
593208    351360  2018-02-09 10:29:45     viewed product  40ae94b8   
2130049     8564  2018-05-19 22:21:47    ad campaign hit  e916d8b4   
461964     10484  2018-05-19 15:05:42    ad campaign hit  3250bb4c   
1194320    48239  2018-05-30 01:57:13     viewed product  82b456c0   
266863   1479345  2018-05-23 02:03:38     viewed product  1be0be2b   
1110290  1532355  2018-05-27 13:22:55     viewed product  7864d948   
209368    357525  2018-02-15 01:49:32     viewed product  161e6408   
671935     73291  2018-05-15 21:22:56     viewed product  486eb592   
2017804   626398  2018-05-14 14:31:48     viewed product  ddac5f39   
2230839   869790  2018-05-25 18:10:31  searched products  f4251a9e   
1910286  1110881  2018-05-24 00:32:33     viewed product  d21b879f   
1338625   287854  2018-05-02 17:08:03     viewed product  9310095f   
263462     28740  2018-05-19 21:06:47     viewed product  1b6dcd58   
1814537  1732883  2018-04-05 12:55:40    ad campaign hit  c7a80a5a   
341702    480487  2018-05-30 18:30:30    ad campaign hit  2476f804   
85671    1896337  2018-05-24 15:56:17      brand listing  095d6adb   
2186525  1581070  2018-05-24 13:30:11     viewed product  ef4cac3e   
50309       6221  2018-05-19 17:23:10    ad campaign hit  0582076c   
2289574   191734  2018-05-18 15:31:18     viewed product  fa73d2ba   
1988971  1528403  2018-05-18 12:32:36     viewed product  da719dc1   
1943692   474855  2018-05-24 12:31:34     viewed product  d62e8d2a   
771081    862878  2018-05-29 14:24:01     viewed product  5380ef50   
659918   2068234  2018-05-24 17:10:10    generic listing  46c2a2b2   
690877    532593  2018-05-28 16:49:56     viewed product  4a714c7b   
749889   1982757  2018-05-15 16:27:44    generic listing  51260be1   
1934680  1277070  2018-05-30 16:36:27    ad campaign hit  d529d7d1   
1315461  1877250  2018-05-18 15:36:30      brand listing  904f1c23   
1882443  1792487  2018-05-22 16:50:51    generic listing  cf09301f   
1584475  1242984  2018-05-21 21:45:48  search engine hit  ad782806   
2145089   653461  2018-03-29 11:47:23     viewed product  ea8492e2   
1423447  1137530  2018-05-18 02:32:46     viewed product  9c2b6f94   
2021774    46272  2018-05-30 03:35:40     viewed product  ddf54e41   
12156    1377105  2018-04-02 04:17:08     viewed product  016b86b9   
2104927  1357219  2018-04-15 02:43:44  search engine hit  e6575149   
1953321  2221068  2018-05-16 21:34:38       visited site  d7114e56   
914983   1624059  2018-05-30 21:10:57     viewed product  636a3818   
1704994  1674637  2018-04-15 02:45:24  searched products  bb67c35a   
776136   2323909  2018-05-21 20:50:47       visited site  53fced54   
1568636  1698057  2018-05-03 00:24:46  searched products  abd61dd4   
...          ...                  ...                ...       ...   
1573888    29235  2018-05-19 18:35:27     viewed product  ac5d4f7c   
169843   1803513  2018-05-18 22:38:02    generic listing  11d464f0   
1450358  2256447  2018-05-29 00:57:01       visited site  9e86c41c   
624362    545900  2018-05-18 02:10:26  searched products  4356db37   
2220701  1632374  2018-05-16 21:00:46     viewed product  f323e87e   
676699   2189620  201

In [22]:
# de los que convirtieron cuantas entradas por campaña hay:
#df[(df.event=='ad campaign hit')&(df.person.isin(convirtieron))].url.value_counts()

In [66]:
df[(df.origen=='old')&(df.event=='conversion')&(df.nombre_mes=='JUNIO')&(df.fecha2<=15)].shape
#df[(df.origen=='old')&(df.event=='conversion')&(df.nombre_mes=='JUNIO')&(df.fecha2<=15)].fecha.value_counts()
#df[(df.origen=='old')&(df.event=='conversion')&(df.nombre_mes=='JUNIO')].shape

(103, 108)

In [168]:
#conv_junio=df[(df.origen=='old')&(df.event=='conversion')&(df.nombre_mes=='JUNIO')&(df.fecha2<=15)].person.unique()

#old_convertions=df[(df.origen=='old')&(df.person.isin(conv_junio)&(df.nombre_mes!='JUNIO'))]

#old_not_conv=df[(df.origen=='old')& (~df.person.isin(conv_junio))]

# b=df[(df.origen=='new')&(df.person.isin(conv_junio))] # esto da cero filas ! así que está ok.

#old_convertions.sample(100)



#df_x=df[df.person.isin(df1.person.unique())]

#df=pd.concat([df_x, old_convertions])

#df_x.sample(10)

df.shape

(2342337, 108)

In [27]:
df.columns

Index(['index', 'timestamp', 'event', 'person', 'url', 'sku', 'model',
       'condition', 'storage', 'color', 'skus', 'search_term', 'staticpage',
       'campaign_source', 'search_engine', 'channel', 'new_vs_returning',
       'city', 'region', 'country', 'device_type', 'screen_resolution',
       'operating_system_version', 'browser_version', 'timestamp2',
       'timestamp_anterior', 'persona_anterior', 'time_diff',
       'tiempo_conv_mins', 'fecha', 'month', 'day', 'nombre_mes', 'fecha2',
       'dia', 'lunes', 'martes', 'miercoles', 'jueves', 'viernes', 'sabado',
       'domingo', 'week', 'flag_week', 'flag_weekend', 'brand_viewed', 'visit',
       'viewprod', 'checkout', 'brand_listing', 'ad_camp_hit',
       'generic_listing', 'searched_products', 'search_engine_hit',
       'conversion', 'lead', 'searched_iphone', 'searched_iphone_6s',
       'searched_iphone_7s', 'searched_iphone_7', 'searched_iphone_6',
       'searched_iphone_5', 'searched_samsung', 'searched_sony',
      

In [40]:
#df.groupby(['person']).agg({'col3':'sum','col4':'sum'})


df_grouped=df.groupby(['person']).agg({
    
'tiempo_conv_mins':'mean',
'fecha':'max',
'month':'max',
'fecha2':'max',
'day':'max',
'lunes':'sum',
'martes':'sum',
'miercoles':'sum',
'jueves':'sum',
'viernes':'sum',
'sabado':'sum',
'domingo':'sum',
'flag_week':'sum',
'flag_weekend':'sum',

'visit':'sum',
'viewprod':'sum',
'checkout':'sum',
'brand_listing':'sum',
'ad_camp_hit':'sum',
'generic_listing':'sum',
'searched_products':'sum',
'search_engine_hit':'sum',
'conversion':'sum',
'lead':'sum',
'searched_iphone':'sum',
'searched_iphone_6s':'sum',
'searched_iphone_7s':'sum',
'searched_iphone_7':'sum',
'searched_iphone_6':'sum',
'searched_iphone_5':'sum',
'searched_samsung':'sum',
'searched_sony':'sum',
'searched_xperia':'sum',
'searched_motorola':'sum',
'searched_a5':'sum',
'searched_a7':'sum',
'searched_j2':'sum',
'searched_j3':'sum',
'searched_j4':'sum',
'searched_j5':'sum',
'searched_j6':'sum',
'searched_j7':'sum',
'searched_s6':'sum',
'searched_s7':'sum',
'searched_s8':'sum',
'searched_moto_g':'sum',
'searched_moto':'sum',
'searched_galaxy':'sum',
'searched_lg':'sum',
'searched_asus':'sum',
'iphone_se_viewed':'sum',
'iphone_5_viewed':'sum',
'iphone_6_viewed':'sum',
'iphone_7_viewed':'sum',
'samsung_s8_plus':'sum',
'samsung_s8':'sum',
'samsung_s7':'sum',
'samsung_s6':'sum',
'samsung_s5':'sum',
'samsung_s7_viewed':'sum',
'samsung_s6_viewed':'sum',
'samsung_note':'sum',
'samsung_note_8':'sum',
'samsung_a7':'sum',
'samsung_a8':'sum',
'samsung_a5':'sum',
'samsung_j7':'sum',
'samsung_j5':'sum',
'samsung_j4':'sum',
'samsung_j3':'sum',
'samsung_j2':'sum',
'samsung_j1':'sum',
'moto_g5':'sum',
'moto_g4':'sum',
'moto_g3':'sum',
'moto_g2':'sum',
'moto_g':'sum',
'moto_z':'sum',
'moto_x_play':'sum',
'moto_x2':'sum',
'moto_x':'sum',
'moto_e2':'sum',
'xperia_m4':'sum',
'xperia_z':'sum',
'xperia_z2':'sum',
'xperia_z3':'sum',
'xperia_z4':'sum',
'xperia_z5':'sum',
'iphone_se_viewed_cho':'sum',
'iphone_5_viewed_cho':'sum',
'iphone_6_viewed_cho':'sum',
'iphone_7_viewed_cho':'sum',
'samsung_s8_plus_cho':'sum',
'samsung_s8_cho':'sum',
'samsung_s7_cho':'sum',
'samsung_s6_cho':'sum',
'samsung_s5_cho':'sum',
'samsung_s7_viewed_cho':'sum',
'samsung_s6_viewed_cho':'sum',
'samsung_note_cho':'sum',
'samsung_note_8_cho':'sum',
'samsung_a7_cho':'sum',
'samsung_a8_cho':'sum',
'samsung_a5_cho':'sum',
'samsung_j7_cho':'sum',
'samsung_j5_cho':'sum',
'samsung_j4_cho':'sum',
'samsung_j3_cho':'sum',
'samsung_j2_cho':'sum',
'samsung_j1_cho':'sum',
'moto_g5_cho':'sum',
'moto_g4_cho':'sum',
'moto_g3_cho':'sum',
'moto_g2_cho':'sum',
'moto_g_cho':'sum',
'moto_z_cho':'sum',
'moto_x_play_cho':'sum',
'moto_x2_cho':'sum',
'moto_x_cho':'sum',
'moto_e2_cho':'sum',
'xperia_m4_cho':'sum',
'xperia_z_cho':'sum',
'xperia_z2_cho':'sum',
'xperia_z3_cho':'sum',
'xperia_z4_cho':'sum',
'xperia_z5_cho':'sum',
'iphone_se_viewed_conv':'sum',
'iphone_5_viewed_conv':'sum',
'iphone_6_viewed_conv':'sum',
'iphone_7_viewed_conv':'sum',
'samsung_s8_plus_conv':'sum',
'samsung_s8_conv':'sum',
'samsung_s7_conv':'sum',
'samsung_s6_conv':'sum',
'samsung_s5_conv':'sum',
'samsung_s7_viewed_conv':'sum',
'samsung_s6_viewed_conv':'sum',
'samsung_note_conv':'sum',
'samsung_note_8_conv':'sum',
'samsung_a7_conv':'sum',
'samsung_a8_conv':'sum',
'samsung_a5_conv':'sum',
'samsung_j7_conv':'sum',
'samsung_j5_conv':'sum',
'samsung_j4_conv':'sum',
'samsung_j3_conv':'sum',
'samsung_j2_conv':'sum',
'samsung_j1_conv':'sum',
'moto_g5_conv':'sum',
'moto_g4_conv':'sum',
'moto_g3_conv':'sum',
'moto_g2_conv':'sum',
'moto_g_conv':'sum',
'moto_z_conv':'sum',
'moto_x_play_conv':'sum',
'moto_x2_conv':'sum',
'moto_x_conv':'sum',
'moto_e2_conv':'sum',
'xperia_m4_conv':'sum',
'xperia_z_conv':'sum',
'xperia_z2_conv':'sum',
'xperia_z3_conv':'sum',
'xperia_z4_conv':'sum',
'xperia_z5_conv':'sum',
'condition_bom':'sum',
'condition_excelente':'sum',
'condition_muito_bom':'sum',
'condition_touch':'sum',
'condition_novo':'sum',
'condition_bom_cho':'sum',
'condition_excelente_cho':'sum',
'condition_muito_bom_cho':'sum',
'condition_touch_cho':'sum',
'condition_novo_cho':'sum',
'condition_bom_conv':'sum',
'condition_excelente_conv':'sum',
'condition_muito_bom_conv':'sum',
'condition_touch_conv':'sum',
'condition_novo_conv':'sum',
'searched_google':'sum',
'searched_bing':'sum',
'searched_yahoo':'sum',
'iphone_viewed':'sum',
'samsung_viewed':'sum',
'motorola_viewed':'sum',
'sony_viewed':'sum',
'lg_viewed':'sum',
'asus_viewed':'sum',
'ipad_viewed':'sum',
'storage_8':'sum',
'storage_16':'sum',
'storage_32':'sum',
'storage_64':'sum',
'storage_128':'sum',
'storage_4':'sum',
'storage_256':'sum',
'storage_512MB':'sum',
'visit_mayo':'sum',
'visit_abril':'sum',
'visit_marzo':'sum',
'visit_febrero':'sum',
'visit_enero':'sum',
'conv_mayo':'sum',
'conv_abril':'sum',
'conv_marzo':'sum',
'conv_febrero':'sum',
'conv_enero':'sum',
'busqueda_term':'sum',
'sist_oper_windows':'sum',
'sist_oper_android':'sum',
'sist_oper_ios':'sum',
'sist_oper_mac':'sum',
'sist_oper_linux':'sum',
'col_preto':'sum',
'col_dourado':'sum',
'col_cinza':'sum',
'col_branco':'sum',
'col_prateado':'sum',
'col_rosa':'sum',
'camp_google':'sum',
'camp_criteo':'sum',
'camp_rtbhouse':'sum',
'camp_zanox':'sum',
'CHO_MAYO':'sum',
'CHO_ABRIL':'sum',
'CHO_MARZO':'sum',
'CHO_FEBRERO':'sum',
'CHO_ENERO':'sum',
'chan_paid':'sum',
'chan_direct':'sum',
'chan_referral':'sum',
'chan_organic':'sum',
'nvsr_return':'sum',
'nvsr_new':'sum',
'city_saopaulo':'sum',
'city_rio':'sum',
'city_belo':'sum',
'city_salv':'sum',
'disp_smart':'sum',
'disp_comp':'sum',
'disp_tablet':'sum',
'res_360x640':'sum',
'res_1366x768':'sum',
'res_1920x1080':'sum',
'Primera_Semana':'sum',
'Segunda_Semana':'sum',
'Tercera_Semana':'sum',
'Cuarta_Semana':'sum',
'Fin_de_Mes':'sum',
'iphone_1eraSem':'sum',
'iphone_2daSem':'sum',
'iphone_3eraSem':'sum',
'iphone_4taSem':'sum',
'iphone_FindeMes':'sum',
'samsung_1eraSem':'sum',
'samsung_2daSem':'sum',
'samsung_3eraSem':'sum',
'samsung_4taSem':'sum',
'samsung_FindeMes':'sum',
'motorola_1eraSem':'sum',
'motorola_2daSem':'sum',
'motorola_3eraSem':'sum',
'motorola_4taSem':'sum',
'motorola_FindeMes':'sum',
'Iphonese_FindeMes':'sum',
'Iphone5_FindeMes':'sum',
'Iphone6_FindeMes':'sum',
'Iphone7_FindeMes':'sum',
'galaxy_s8_plus_FindeMes':'sum',
'galaxy_s8_FindeMes':'sum',
'galaxy_s7_FindeMes':'sum',
'galaxy_s6_FindeMes':'sum',
'galaxy_s5_FindeMes':'sum',
'galaxy_s3_FindeMes':'sum',
'galaxy_s7_edge_FindeMes':'sum',
'galaxy_s6_edge_FindeMes':'sum',
'galaxy_note_FindeMes':'sum',
'galaxy_a7_FindeMes':'sum',
'galaxy_a8_FindeMes':'sum',
'galaxy_a5_FindeMes':'sum',
'galaxy_j7_FindeMes':'sum',
'galaxy_j5_FindeMes':'sum',
'galaxy_j4_FindeMes':'sum',
'galaxy_j3_FindeMes':'sum',
'galaxy_j2_FindeMes':'sum',
'galaxy_j1_FindeMes':'sum',
'moto_g5_FindeMes':'sum',
'moto_g4_FindeMes':'sum',
'moto_g3_FindeMes':'sum',
'moto_g2_FindeMes':'sum',
'moto_g_FindeMes':'sum',
'moto_z_FindeMes':'sum',
'xplay_FindeMes':'sum',
'moto_x2_FindeMes':'sum',
'moto_x_FindeMes':'sum',
'moto_e2_FindeMes':'sum',
'xperia_m4_FindeMes':'sum',
'xperia_z_FindeMes':'sum',
'xperia_z2_FindeMes':'sum',
'xperia_z3_FindeMes':'sum',
'xperia_z4_FindeMes':'sum',
'xperia_z5_FindeMes':'sum',
'Iphonese_1eraSemana':'sum',
'Iphone5_1eraSemana':'sum',
'Iphone6_1eraSemana':'sum',
'Iphone7_1eraSemana':'sum',
'galaxy_s8_plus_1eraSemana':'sum',
'galaxy_s8_1eraSemana':'sum',
'galaxy_s7_1eraSemana':'sum',
'galaxy_s6_1eraSemana':'sum',
'galaxy_s5_1eraSemana':'sum',
'galaxy_s3_1eraSemana':'sum',
'galaxy_s7_edge_1eraSemana':'sum',
'galaxy_s6_edge_1eraSemana':'sum',
'galaxy_note_1eraSemana':'sum',
'galaxy_a7_1eraSemana':'sum',
'galaxy_a8_1eraSemana':'sum',
'galaxy_a5_1eraSemana':'sum',
'galaxy_j7_1eraSemana':'sum',
'galaxy_j5_1eraSemana':'sum',
'galaxy_j4_1eraSemana':'sum',
'galaxy_j3_1eraSemana':'sum',
'galaxy_j2_1eraSemana':'sum',
'galaxy_j1_1eraSemana':'sum',
'moto_g5_1eraSemana':'sum',
'moto_g4_1eraSemana':'sum',
'moto_g3_1eraSemana':'sum',
'moto_g2_1eraSemana':'sum',
'moto_g_1eraSemana':'sum',
'moto_z_1eraSemana':'sum',
'xplay_1eraSemana':'sum',
'moto_x2_1eraSemana':'sum',
'moto_x_1eraSemana':'sum',
'moto_e2_1eraSemana':'sum',
'xperia_m4_1eraSemana':'sum',
'xperia_z_1eraSemana':'sum',
'xperia_z2_1eraSemana':'sum',
'xperia_z3_1eraSemana':'sum',
'xperia_z4_1eraSemana':'sum',
'xperia_z5_1eraSemana':'sum',
'Iphonese_2daSemana':'sum',
'Iphone5_2daSemana':'sum',
'Iphone6_2daSemana':'sum',
'Iphone7_2daSemana':'sum',
'galaxy_s8_plus_2daSemana':'sum',
'galaxy_s8_2daSemana':'sum',
'galaxy_s7_2daSemana':'sum',
'galaxy_s6_2daSemana':'sum',
'galaxy_s5_2daSemana':'sum',
'galaxy_s3_2daSemana':'sum',
'galaxy_s7_edge_2daSemana':'sum',
'galaxy_s6_edge_2daSemana':'sum',
'galaxy_note_2daSemana':'sum',
'galaxy_a7_2daSemana':'sum',
'galaxy_a8_2daSemana':'sum',
'galaxy_a5_2daSemana':'sum',
'galaxy_j7_2daSemana':'sum',
'galaxy_j5_2daSemana':'sum',
'galaxy_j4_2daSemana':'sum',
'galaxy_j3_2daSemana':'sum',
'galaxy_j2_2daSemana':'sum',
'galaxy_j1_2daSemana':'sum',
'moto_g5_2daSemana':'sum',
'moto_g4_2daSemana':'sum',
'moto_g3_2daSemana':'sum',
'moto_g2_2daSemana':'sum',
'moto_g_2daSemana':'sum',
'moto_z_2daSemana':'sum',
'xplay_2daSemana':'sum',
'moto_x2_2daSemana':'sum',
'moto_x_2daSemana':'sum',
'moto_e2_2daSemana':'sum',
'xperia_m4_2daSemana':'sum',
'xperia_z_2daSemana':'sum',
'xperia_z2_2daSemana':'sum',
'xperia_z3_2daSemana':'sum',
'xperia_z4_2daSemana':'sum',
'xperia_z5_2daSemana':'sum',
'Iphonese_3eraSemana':'sum',
'Iphone5_3eraSemana':'sum',
'Iphone6_3eraSemana':'sum',
'Iphone7_3eraSemana':'sum',
'galaxy_s8_plus_3eraSemana':'sum',
'galaxy_s8_3eraSemana':'sum',
'galaxy_s7_3eraSemana':'sum',
'galaxy_s6_3eraSemana':'sum',
'galaxy_s5_3eraSemana':'sum',
'galaxy_s3_3eraSemana':'sum',
'galaxy_s7_edge_3eraSemana':'sum',
'galaxy_s6_edge_3eraSemana':'sum',
'galaxy_note_3eraSemana':'sum',
'galaxy_a7_3eraSemana':'sum',
'galaxy_a8_3eraSemana':'sum',
'galaxy_a5_3eraSemana':'sum',
'galaxy_j7_3eraSemana':'sum',
'galaxy_j5_3eraSemana':'sum',
'galaxy_j4_3eraSemana':'sum',
'galaxy_j3_3eraSemana':'sum',
'galaxy_j2_3eraSemana':'sum',
'galaxy_j1_3eraSemana':'sum',
'moto_g5_3eraSemana':'sum',
'moto_g4_3eraSemana':'sum',
'moto_g3_3eraSemana':'sum',
'moto_g2_3eraSemana':'sum',
'moto_g_3eraSemana':'sum',
'moto_z_3eraSemana':'sum',
'xplay_3eraSemana':'sum',
'moto_x2_3eraSemana':'sum',
'moto_x_3eraSemana':'sum',
'moto_e2_3eraSemana':'sum',
'xperia_m4_3eraSemana':'sum',
'xperia_z_3eraSemana':'sum',
'xperia_z2_3eraSemana':'sum',
'xperia_z3_3eraSemana':'sum',
'xperia_z4_3eraSemana':'sum',
'xperia_z5_3eraSemana':'sum',
'Iphonese_4taSemana':'sum',
'Iphone5_4taSemana':'sum',
'Iphone6_4taSemana':'sum',
'Iphone7_4taSemana':'sum',
'galaxy_s8_plus_4taSemana':'sum',
'galaxy_s8_4taSemana':'sum',
'galaxy_s7_4taSemana':'sum',
'galaxy_s6_4taSemana':'sum',
'galaxy_s5_4taSemana':'sum',
'galaxy_s3_4taSemana':'sum',
'galaxy_s7_edge_4taSemana':'sum',
'galaxy_s6_edge_4taSemana':'sum',
'galaxy_note_4taSemana':'sum',
'galaxy_a7_4taSemana':'sum',
'galaxy_a8_4taSemana':'sum',
'galaxy_a5_4taSemana':'sum',
'galaxy_j7_4taSemana':'sum',
'galaxy_j5_4taSemana':'sum',
'galaxy_j4_4taSemana':'sum',
'galaxy_j3_4taSemana':'sum',
'galaxy_j2_4taSemana':'sum',
'galaxy_j1_4taSemana':'sum',
'moto_g5_4taSemana':'sum',
'moto_g4_4taSemana':'sum',
'moto_g3_4taSemana':'sum',
'moto_g2_4taSemana':'sum',
'moto_g_4taSemana':'sum',
'moto_z_4taSemana':'sum',
'xplay_4taSemana':'sum',
'moto_x2_4taSemana':'sum',
'moto_x_4taSemana':'sum',
'moto_e2_4taSemana':'sum',
'xperia_m4_4taSemana':'sum',
'xperia_z_4taSemana':'sum',
'xperia_z2_4taSemana':'sum',
'xperia_z3_4taSemana':'sum',
'xperia_z4_4taSemana':'sum',
'xperia_z5_4taSemana':'sum',

'camp_emblue':'sum',
'camp_afilio':'sum',
'camp_manifest':'sum',
'camp_facebookads':'sum',
'camp_voxus':'sum',
'camp_rakuten':'sum',
'camp_bing':'sum',
'camp_datacrush':'sum',
'camp_indexa':'sum',
'camp_buscape':'sum',
'camp_facebook':'sum',
'camp_afiliado':'sum',
'camp_otros':'sum',
'url_comprar':'sum',
'url_vender':'sum',
'url_iphone':'sum',
'url_samsung':'sum',
'url_motorola':'sum',
'url_lg':'sum',
'url_ipad':'sum',
'url_asus':'sum',
'url_apple':'sum',
'url_sony':'sum',
'url_quantum':'sum',
'url_6s':'sum',
'url_6':'sum',
'url_iphone-5s':'sum',
'url_galaxy':'sum',
'url_galaxy-j5':'sum',
'galaxy-s7':'sum',
'url_galaxy-s6':'sum',
'url_galaxy-j7':'sum',
'url_galaxy-s8':'sum'

})



In [33]:
df_grouped.sample(100)

tiempo_conv_mins      fecha  month  fecha2  day  lunes  martes  \
person                                                                     
086b64ea          2.256790 2018-05-30      5       3   30    0.0     0.0   
75b121ac               NaN 2018-05-26      5       6   26    0.0     0.0   
0256b30a       1565.547126 2018-05-28      5       1   28   58.0     0.0   
406f9a75               NaN 2018-05-24      5       4   24    0.0     0.0   
35bcbc7c          0.072222 2018-05-30      5       3   30    0.0     0.0   
a83856a2        484.259884 2018-05-30      5       3   30    0.0    20.0   
9a0524b8          4.393590 2018-05-17      5       4   17    0.0     0.0   
71cc441a        847.164130 2018-05-27      5       7   27    0.0    18.0   
36474151        477.843939 2018-05-25      5       5   25    0.0     6.0   
e906fc0b       1783.749254 2018-05-17      5       4   17   25.0    39.0   
19faf3af          0.066667 2018-05-18      5       5   18    0.0     0.0   
d191d46d          0.125000 2018-05-30      5       3   30    0.0     0.0   
b203cdce      14935.670833 2018-05-27      5       7   27    0.0     0.0   
8ca30177         32.205392 2018-05-20      5       7   20    0.0     0.0   
18bf8f3e          0.123333 2018-05-25      5       5   25    0.0     0.0   
e494186a          0.312069 2018-05-26      5       6   26    0.0     0.0   
9711f755        157.615870 2018-05-31      5       7   31   50.0    30.0   
c8626e17        579.822396 2018-05-25      5       6   25    0.0     0.0   
e7b2370b         42.086036 2018-05-29      5       2   29   26.0    12.0   
61fdc00d        283.253704 2018-05-30      5       7   30    0.0     0.0   
993ac67f        913.922917 2018-05-21      5       3   21    5.0     0.0   
eaa87944        230.308333 2018-05-29      5       2   29    1.0     6.0   
4ecb305d          0.384058 2018-05-17      5       4   17    0.0     0.0   
1e1f9bb6          0.188889 2018-05-19      5       6   19    0.0     0.0   
0c8c5c94          0.396212 2018-05-25      5       5   25    0.0     0.0   
8dcd6543          0.650000 2018-05-29      5       2   29    0.0     9.0   
abc01fe5        108.153333 2018-05-27      5       7   27    0.0     0.0   
a2dd0f8e          0.072222 2018-05-27      5       7   27    0.0     0.0   
785d6a3a        897.172857 2018-05-31      5       4   31    8.0    62.0   
b7656d4a          0.187500 2018-05-20      5       7   20    0.0     0.0   
8eb8bfe9          0.214815 2018-05-28      5       1   28   10.0     0.0   
34445e57       2191.825000 2018-05-01      5       2    1    0.0     4.0   
91db9d63       2765.938889 2018-05-27      5       7   27    0.0     0.0   
e5dc5359        437.877143 2018-05-23      5       6   23    0.0     0.0   
4d785c7d          4.955556 2018-05-16      5       3   16    0.0     0.0   
e1eff058          0.433333 2018-05-25      5       5   25    0.0     0.0   
0cffd1be        301.926735 2018-05-31      5       4   31   19.0    46.0   
44c7e26e        160.624074 2018-05-21      5       7   21    3.0     0.0   
dd988d26         59.017111 2018-05-28      5       5   28    5.0     0.0   
d75464b8         23.316947 2018-05-30      5       3   30   17.0    33.0   
19988c86       1524.882018 2018-05-29      5       2   29   16.0    22.0   
809ed67b        679.085714 2018-05-25      5       5   25    0.0     0.0   
d0721a3e        344.500362 2018-05-22      5       6   22    7.0   102.0   
2ccaed25        318.034827 2018-05-31      5       6   31   69.0     0.0   
b591c8d1         36.392353 2018-05-27      5       7   27    0.0   108.0   
de7c12fe          0.366667 2018-05-16      5       3   16    0.0     0.0   
e1823a92        382.512778 2018-05-25      5       5   25    0.0     0.0   
422438f8          1.651852 2018-05-30      5       3   30    0.0     0.0   
044bbf67        207.841892 2018-05-30      5       6   30   14.0    26.0   
f427fb1b          0.602381 2018-05-21      5       1   21    8.0     0.0   
dc3e68d9        103.676864 2018-05-31      5       7   31 

In [41]:


# Ratios:
df_grouped['r_conv_visit']=df_grouped['conversion']/df_grouped['visit']
df_grouped['r_conv_cho']=df_grouped['conversion']/df_grouped['checkout']
df_grouped['r_cho_conv']=df_grouped['checkout']/df_grouped['conversion']
df_grouped['r_iphone_cho']=df_grouped['checkout']/df_grouped['iphone_viewed']
df_grouped['r_samsung_cho']=df_grouped['checkout']/df_grouped['samsung_viewed']


# ratio conversion y busqueda de términos
df_grouped['r_conv_busq_term']=df_grouped['conversion']/df_grouped['busqueda_term']
df_grouped['r_conv_may_busq_term']=df_grouped['conv_mayo']/df_grouped['busqueda_term']

# ratio de conversion sobre visitas del mes
df_grouped['r_vis_conv_may']=df_grouped['conv_mayo']/df_grouped['visit_mayo']
df_grouped['r_vis_conv_apr']=df_grouped['conv_abril']/df_grouped['visit_abril']
df_grouped['r_vis_conv_mar']=df_grouped['conv_marzo']/df_grouped['visit_marzo']
df_grouped['r_vis_conv_feb']=df_grouped['conv_febrero']/df_grouped['visit_febrero']
df_grouped['r_vis_conv_jan']=df_grouped['conv_enero']/df_grouped['visit_enero']
# idem pero meses distintos:
df_grouped['r_conv_may_vis_apr']=df_grouped['conv_mayo']/df_grouped['visit_abril']
df_grouped['r_conv_apr_vis_mar']=df_grouped['conv_abril']/df_grouped['visit_marzo']
df_grouped['r_conv_mar_vis_feb']=df_grouped['conv_marzo']/df_grouped['visit_febrero']


#df.loc[df.event=='checkout','checkout']=1
df_grouped['r_cho_vis_may']=df_grouped['checkout']/df_grouped['visit_mayo']

# sistema operativo ratios:
df_grouped['r_cho_windows']=df_grouped['checkout']/df_grouped['sist_oper_windows']
df_grouped['r_conv_windows']=df_grouped['conversion']/df_grouped['sist_oper_windows']
df_grouped['r_conv_may_windows']=df_grouped['conv_mayo']/df_grouped['sist_oper_windows']

# viewprod
df_grouped['r_vis_may_viewprod']=df_grouped['visit_mayo']/df_grouped['viewprod']
df_grouped['r_conv_viewprod']=df_grouped['conversion']/df_grouped['viewprod']
df_grouped['r_condbom_viewprod']=df_grouped['condition_bom']/df_grouped['viewprod']


# Magic:
df_grouped['conv_cho_vis_may']=(df_grouped['conversion']+df_grouped['checkout'])/df_grouped['visit_mayo']
df_grouped['vis_may_cho_conv']=(df_grouped['visit_mayo']+df_grouped['checkout'])/df_grouped['conversion']


# promedios por mes:
df_grouped['prom_conv_mes']=df_grouped['conversion']/5
df_grouped['prom_cho_mes']=df_grouped['checkout']/5

# cantidad de meses distintos en los que convirtió: TBD


# Ratios de campaña:
df_grouped['r_conv_may_camp_hit']=df_grouped['conv_mayo']/df_grouped['ad_camp_hit']
df_grouped['r_vis_may_camp_hit']=df_grouped['visit_mayo']/df_grouped['ad_camp_hit']
df_grouped['r_cho_camp_hit']=df_grouped['checkout']/df_grouped['ad_camp_hit']
df_grouped['r_conv_camp_hit']=df_grouped['conversion']/df_grouped['ad_camp_hit']
df_grouped['r_viewp_camp_hit']=df_grouped['viewprod']/df_grouped['ad_camp_hit']
df_grouped['r_cond_bom_camp_hit']=df_grouped['condition_bom']/df_grouped['ad_camp_hit']
df_grouped['r_search_eng_camp_hit']=df_grouped['search_engine_hit']/df_grouped['ad_camp_hit']


# Ratios de busqueda de termino:
df_grouped['r_conv_busqterm']=df_grouped['conversion']/df_grouped['busqueda_term']
df_grouped['r_cho_busqterm']=df_grouped['checkout']/df_grouped['busqueda_term']
df_grouped['r_vis_may_busqterm']=df_grouped['visit_mayo']/df_grouped['busqueda_term']
df_grouped['r_viewprod_busqterm']=df_grouped['viewprod']/df_grouped['busqueda_term']

# Ratios condition:
df_grouped['r_conv_conbom']=df_grouped['conversion']/df_grouped['condition_bom']
df_grouped['r_cho_conbom']=df_grouped['checkout']/df_grouped['condition_bom']
df_grouped['r_vis_may_conbom']=df_grouped['visit_mayo']/df_grouped['condition_bom']
df_grouped['r_conv_conmuybom']=df_grouped['conversion']/df_grouped['condition_muito_bom']
df_grouped['r_cho_conmuybom']=df_grouped['checkout']/df_grouped['condition_muito_bom']
df_grouped['r_vis_may_conmuybom']=df_grouped['visit_mayo']/df_grouped['condition_muito_bom']
df_grouped['r_conv_conexc']=df_grouped['conversion']/df_grouped['condition_excelente']
df_grouped['r_cho_conexc']=df_grouped['checkout']/df_grouped['condition_excelente']
df_grouped['r_vis_may_conexc']=df_grouped['visit_mayo']/df_grouped['condition_excelente']

# % del total:
denominador=df_grouped.size # a esto lo uso como denominador
df_grouped['pt_cho']=df_grouped['checkout']/denominador
df_grouped['pt_conv']=df_grouped['conversion']/denominador
df_grouped['pt_conv_may']=df_grouped['conv_mayo']/denominador
df_grouped['pt_conv_apr']=df_grouped['conv_abril']/denominador
df_grouped['pt_conv_mar']=df_grouped['conv_marzo']/denominador
df_grouped['pt_vis_may']=df_grouped['visit_mayo']/denominador
df_grouped['pt_viewprod']=df_grouped['viewprod']/denominador


# Reemplazo los inf por Nan:
#df_grouped=df_grouped.replace([np.inf, -np.inf], np.nan)

# Reemplazo los Nan por 0:
#df_grouped=df_grouped.fillna(0)



# Pego la clase:
df_grouped_2 = pd.merge(df_grouped,df_labels,on='person',how='left').reset_index()




In [35]:
df_grouped_2.sample(100)

index    person  tiempo_conv_mins      fecha  month  fecha2  day  \
14348  14348  62ddf12d         54.661772 2018-05-30      5       5   30   
33721  33721  e8454ebf        109.764912 2018-05-31      5       4   31   
35134  35134  f23a2f1b        231.682051 2018-05-27      5       7   27   
16404  16404  714f29f1       2676.301667 2018-05-24      5       5   24   
4389    4389  1ea06dc4          0.105556 2018-05-22      5       2   22   
6617    6617  2df6bc0c        309.523333 2018-05-30      5       6   30   
10352  10352  478e8618        615.656481 2018-05-25      5       5   25   
16657  16657  7326c390       1146.994974 2018-05-29      5       6   29   
32220  32220  de4da42a               NaN 2018-05-21      5       1   21   
19716  19716  88b91c5d               NaN 2018-05-20      5       7   20   
26829  26829  b95b634e        864.613522 2018-05-31      5       5   31   
23311  23311  a103c5e5        356.433463 2018-05-30      5       7   30   
4412    4412  1ec1911d        387.929396 2018-05-27      5       7   27   
452      452  03439225        444.325481 2018-05-31      5       7   31   
23463  23463  a21c67ff       6664.247531 2018-05-29      5       2   29   
24308  24308  a80267a9         74.580952 2018-05-30      5       7   30   
18995  18995  83c1d88f          0.038889 2018-05-14      5       1   14   
30920  30920  d544fb6d        657.724359 2018-05-30      5       4   30   
27851  27851  c04d4a65          0.111667 2018-05-30      5       3   30   
6757    6757  2ef45681       1714.051515 2018-05-10      5       4   10   
23644  23644  a361ca9d         18.806667 2018-05-31      5       4   31   
26446  26446  b6d9167e         73.344969 2018-05-31      5       4   31   
17872  17872  7bbc47be          3.180000 2018-05-25      5       5   25   
35055  35055  f1bdcbdb        137.715982 2018-05-31      5       6   31   
31170  31170  d70fb702        112.572685 2018-05-20      5       7   20   
13918  13918  5fcea5de          1.803968 2018-05-30      5       3   30   
28706  28706  c679007a         51.965226 2018-05-16      5       4   16   
3972    3972  1b6dcd58         30.964521 2018-05-22      5       6   22   
24458  24458  a919cebd          3.183333 2018-05-21      5       1   21   
28562  28562  c51a7e46         89.019109 2018-05-25      5       7   25   
12373  12373  551fad73          0.878922 2018-05-23      5       3   23   
31272  31272  d7c0065f        823.596212 2018-05-29      5       6   29   
17921  17921  7c0d8ee1         65.295614 2018-05-20      5       7   20   
28175  28175  c292c287          0.055556 2018-05-29      5       2   29   
15844  15844  6d187a5d       3736.484568 2018-05-30      5       5   30   
35888  35888  f73ecac0          2.498148 2018-05-29      5       2   29   
4731    4731  210edfc9          0.254762 2018-05-29      5       2   29   
25047  25047  ad0856a7        145.317333 2018-05-25      5       7   25   
1460    1460  0a3f6017        120.833333 2018-05-22      5       5   22   
32235  32235  de61a233         83.525000 2018-05-23      5       3   23   
3692    3692  1986c65a          0.266667 2018-05-29      5       2   29   
12455  12455  55a2402a          0.526667 2018-05-21      5       1   21   
11466  11466  4f06f2dd        160.706818 2018-05-22      5       5   22   
2723    2723  131d32de          0.033333 2018-05-29      5       2   29   
18254  18254  7e60e5ee          0.792857 2018-05-24      5       4   24   
6540    6540  2d68604a      11249.911111 2018-05-16      5       3   16   
37099  37099  ffa0d7a0        680.625000 2018-05-15      5       4   15   
32613  32613  e0f08865       2610.164583 2018-05-21      5       3   21   
3034    3034  1530d5e9          1.336667 2018-05-31      5       4   31   
32237  32237  de6257e8         12.253435 2018-05-29      5       2   29   
31206  31206  d748432c       1231.576667 2018-05-22      5       4   22   
27571  27571  be5c219e          0.027778 2018-05-30      5       3   30   
20405  20405  8d8eff10          

In [42]:
df_grouped_2.shape

(38829, 543)

In [43]:
#Bajada del dataset a csv:
df_grouped_2.to_csv(path_or_buf='/Users/jpascual/Documents/Personal/Orga_datos_7506/TP2/tp2_orga_datos/df_grouped_v4.csv')

In [39]:
# Bajo la data cruda por las dudas:
df.to_csv(path_or_buf='/Users/jpascual/Documents/Personal/Orga_datos_7506/TP2/tp2_orga_datos/df_raw_data.csv')

